<a href="https://colab.research.google.com/github/ranim1234/Coach_bot/blob/main/Hawai_Maui_firestore.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install fuzzywuzzy
! pip install geopandas
! pip install geopy
! pip install geohash2

  Preparing metadata (setup.py) ... done
  Created wheel for geohash2: filename=geohash2-1.1-py3-none-any.whl size=15544 sha256=70a3a911add15db5679b4945886bced1f4c3844729a77c53d086e1224335705f
  Stored in directory: /root/.cache/pip/wheels/c0/21/8d/fe65503f4f439aef35193e5ec10a14adc945e20ff87eb35895
Successfully built geohash2


In [2]:
# Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [4]:
import os
import zipfile
import pandas as pd
import geopandas as gpd
import fiona

# Function to extract ZIP files
def extract_zip_files(zip_file, extract_to):
    with zipfile.ZipFile(zip_file, 'r') as zip_ref:
        zip_ref.extractall(extract_to)

# Function to rename columns based on a predefined mapping
def rename_columns(df, column_mapping):
    df.rename(columns=column_mapping, inplace=True)
    return df

# Function to load and explore a dataset
def explore_dataset(path, extract_to, extract_to_zip):
    file_paths = []

    if path.endswith('.zip'):
        extract_zip_files(path, extract_to_zip)
        # Check extracted files and add valid ones to file_paths list
        for root, dirs, files in os.walk(extract_to_zip):
            for name in dirs:
                extracted_file_path = os.path.join(root, name)
                if extracted_file_path.endswith('.gdb'):
                    print(f"Extracted folder: {name}")  # Print the folder name
                    file_paths.append(extracted_file_path)
            for file in files:
                extracted_file_path = os.path.join(root, file)
                print(f"Extracted file: {file}")  # Print the file name
                if extracted_file_path.endswith(('.csv', '.geojson', '.json', '.shp')):
                    file_paths.append(extracted_file_path)
    elif path.endswith(('.csv', '.geojson', '.json', '.shp')) or (os.path.isdir(path) and path.endswith('.gdb')):
        file_name = os.path.basename(path)
        destination_path = os.path.join(extract_to, file_name)
        if not os.path.exists(destination_path):
            os.makedirs(os.path.dirname(destination_path), exist_ok=True)
            os.system(f'cp -r "{path}" "{destination_path}"')
        file_paths.append(destination_path)

    # Column mapping
    column_mapping = {
    'tmk': 'tmk',
    'tmk_txt': 'tmk_txt',
    'cty_tmk': 'cty_tmk',
    'landvalue': 'landval',
    'landexempt': 'landexempt',
    'bldgvalue': 'parval',
    'bldgexempt': 'parexempt',
    'pittcode': 'szip',
    'homeowner': 'owner',
    'nhoodcode': 'nhoodcode',
    'taxacres': 'taxacres',
    'gisacres': 'gisacre',
    'qpub_link': 'zoning_code_link',
    'st_areashape': 'area',
    'st_perimetershape': 'shape'
}

    }

    # Explore the dataset
    for file_path in file_paths:
        if file_path.endswith('.csv'):
            df = pd.read_csv(file_path)
            df = rename_columns(df, column_mapping)
            print(f"\nCSV File: {file_path}")
            print(f"Columns: {df.columns.tolist()}")
            print(df.head(10))
            return df
        elif file_path.endswith('.geojson') or file_path.endswith('.json'):
            gdf = gpd.read_file(file_path)
            gdf = rename_columns(gdf, column_mapping)
            print(f"\nGeoJSON File: {file_path}")
            print(f"Columns: {gdf.columns.tolist()}")
            print(gdf.head(10))
            return gdf
        elif file_path.endswith('.shp'):
            gdf = gpd.read_file(file_path)
            gdf = rename_columns(gdf, column_mapping)
            print(f"\nShapefile: {file_path}")
            print(f"Columns: {gdf.columns.tolist()}")
            print(gdf.head(10))
            return gdf
        elif os.path.isdir(file_path) and file_path.endswith('.gdb'):
            try:
                print([fiona.listlayers(file_path)])
                with fiona.Env(METHOD='SKIP'):
                    for layer in fiona.listlayers(file_path):
                        gdf = gpd.read_file(file_path, layer=layer)
                        gdf = rename_columns(gdf, column_mapping)
                        print(f"\nGDB Folder: {file_path}, Layer: {layer}")
                        print(f"Columns: {gdf.columns.tolist()}")
                        print(gdf.head(10))
                        return gdf
            except Exception as e:
                print(f"Error loading GDB {file_path}: {e}")


# Define paths
extract_to = '/content/extracted_datasets'
extract_to_zip = '/content/extracted_zip'

# Create extraction directories if they do not exist
if not os.path.exists(extract_to):
    os.makedirs(extract_to)
if not os.path.exists(extract_to_zip):
    os.makedirs(extract_to_zip)

# Example usage with different paths
path1 = '/content/drive/MyDrive/landiq/raw/counties/Parcels_-_Maui_County.geojson'

# Explore each dataset individually by calling the function with the specific path
dataset  = explore_dataset(path1, extract_to, extract_to_zip)




GeoJSON File: /content/extracted_datasets/Parcels_-_Maui_County.geojson
Columns: ['objectid', 'tmk', 'tmk_txt', 'cty_tmk', 'landvalue', 'landexempt', 'bldgvalue', 'bldgexempt', 'pittcode', 'homeowner', 'nhoodcode', 'taxacres', 'gisacres', 'qpub_link', 'st_areashape', 'st_perimetershape', 'geometry']
   objectid        tmk    tmk_txt   cty_tmk  landvalue  landexempt  bldgvalue  \
0         1  211001001  211001001  11001001        200         200          0   
1         2  211001002  211001002  11001002       9400        9400          0   
2         3  211001003  211001003  11001003     124900      124900          0   
3         4  211001004  211001004  11001004      35000           0          0   
4         5  211001005  211001005  11001005      16500           0          0   
5         6  211001006  211001006  11001006      17500       17500          0   
6         7  211001007  211001007  11001007      25200           0          0   
7         8  211001008  211001008  11001008      1

In [ ]:
# Filter columns that contain 'description' in their name
description_columns = ['description', 'description2', 'description1']

# Display the first 5 rows of these columns
filtered_df = dataset[description_columns].head(5)
filtered_df

description  description2    description1
0     PLANTATION LAKES     TOWNHOUSE  LOT 16 PHASE 1
1     PLANTATION LAKES     TOWNHOUSE  LOT 15 PHASE 1
2     PLANTATION LAKES     TOWNHOUSE   LOT 7 PHASE 1
3             N/RT 329  TRACT 3 *FX*        E/RT 321
4  VINES CREEK VILLAGE          None          LOT 50

In [ ]:
# Rename the columns
new_column_names = {

    'Description 2': 'property_type',
    'Description 1': 'lot'
}

dataset.rename(columns=new_column_names, inplace=True)

In [ ]:
dataset.columns

Index(['ownfrst', 'ownlast', 'szip', 'Property Depth', 'parcel_id',
       'fire_code', 'additional_info', 'book', 'front_footage', 'landval',
       'zoning_type', 'assessment_value', 'shape_star', 'parcelnumb',
       'object_iD', 'description2', 'school_code', 'mailadd', 'scaled_value',
       'state', 'owner', 'town_code', 'shape', 'city', 'description1',
       'council_district', 'district', 'map', 'description', 'irregular_shape',
       'gisacre', 'improvval', 'taxamt', 'geometry'],
      dtype='object')

In [ ]:
dataset[['city', 'town_code', 'district', 'szip']].head(5)

city town_code  district     szip
0   MILLSBORO        MB     133.0  19966.0
1   MILLSBORO        MB     133.0  19966.0
2   MILLSBORO        MB     133.0  19966.0
3  GEORGETOWN      None     133.0  19947.0
4  WILMINGTON        DA     233.0  19804.0

In [ ]:
# Columns to drop
columns_to_drop = [
    'Property Depth',
    'fire_code',
    'shape_star',
    'object_iD',
    'scaled_value',
    'map',
    'irregular_shape'
]

# Drop the specified columns
dataset.drop(columns=columns_to_drop, inplace=True)


In [ ]:
state_id  = 'de'
county_id  = 'sx'
dataset['parcel_id'] = dataset.apply(lambda row: f"{state_id}-{county_id}-{row['parcelnumb']}", axis=1)


In [ ]:
dataset.head(5)

ownfrst           ownlast     szip    parcel_id additional_info  \
0           PATRICIA            HELWIG  19966.0  de-sx-343.0    TANYA CASSUP   
1  THOMAS & LISA KEE         MARSHALEK  19966.0  de-sx-342.0            None   
2  MEAGHAN ELIZABETH              MOHR  19966.0  de-sx-334.0            None   
3       DAVID MARTIN            PEPPER  19947.0  de-sx-23.07            None   
4               None  2026 VENTURE LLC  19804.0  de-sx-713.0            None   

         book  front_footage  landval zoning_type assessment_value  ...  \
0  D 4110 179           22.0   5000.0        RS 0             None  ...   
1  D 3977 238           22.0   5000.0        RS 0             None  ...   
2  D 4011 310           18.0   5000.0        RS 0             None  ...   
3   D 539 271            NaN      NaN        FG 0             None  ...   
4  D 3420 251           75.0      NaN        TX 0             None  ...   

         shape        city    description1 council_district district  \
0    71.324400   MILLSBORO  LOT 16 PHASE 1              5.0    133.0   
1    71.324500   MILLSBORO  LOT 15 PHASE 1              5.0    133.0   
2    68.886000   MILLSBORO   LOT 7 PHASE 1              5.0    133.0   
3  1167.962987  GEORGETOWN        E/RT 321              2.0    133.0   
4   134.510979  WILMINGTON          LOT 50              5.0    233.0   

           description gisacre  improvval            taxamt  \
0     PLANTATION LAKES     NaN    44500.0  133-16.00-343.00   
1     PLANTATION LAKES     NaN    43500.0  133-16.00-342.00   
2     PLANTATION LAKES     NaN    22700.0  133-16.00-334.00   
3             N/RT 329    8.04        NaN    133-6.00-23.07   
4  VINES CREEK VILLAGE     NaN        NaN  233-11.00-713.00   

                                            geometry  
0  POLYGON ((-8384050.109 4662665.268, -8384050.1...  
1  POLYGON ((-8384041.541 4662665.258, -8384041.5...  
2  POLYGON ((-8384034.478 4662714.131, -8384027.4...  
3  POLYGON ((-8390707.413 4668851.406, -8390913.5...  
4  POLYGON ((-8374845.075 4656982.198, -8374794.2...  

[5 rows x 27 columns]

In [ ]:
from shapely.geometry import shape
from shapely import wkt
def convert_to_polygon(geom):
    if isinstance(geom, str):
        return wkt.loads(geom)
    return geom

dataset['geometry'] = dataset['geometry'].apply(convert_to_polygon)

In [ ]:
dataset.head(5)

ownfrst           ownlast     szip    parcel_id additional_info  \
0           PATRICIA            HELWIG  19966.0  de-sx-343.0    TANYA CASSUP   
1  THOMAS & LISA KEE         MARSHALEK  19966.0  de-sx-342.0            None   
2  MEAGHAN ELIZABETH              MOHR  19966.0  de-sx-334.0            None   
3       DAVID MARTIN            PEPPER  19947.0  de-sx-23.07            None   
4               None  2026 VENTURE LLC  19804.0  de-sx-713.0            None   

         book  front_footage  landval zoning_type assessment_value  ...  \
0  D 4110 179           22.0   5000.0        RS 0             None  ...   
1  D 3977 238           22.0   5000.0        RS 0             None  ...   
2  D 4011 310           18.0   5000.0        RS 0             None  ...   
3   D 539 271            NaN      NaN        FG 0             None  ...   
4  D 3420 251           75.0      NaN        TX 0             None  ...   

         shape        city    description1 council_district district  \
0    71.324400   MILLSBORO  LOT 16 PHASE 1              5.0    133.0   
1    71.324500   MILLSBORO  LOT 15 PHASE 1              5.0    133.0   
2    68.886000   MILLSBORO   LOT 7 PHASE 1              5.0    133.0   
3  1167.962987  GEORGETOWN        E/RT 321              2.0    133.0   
4   134.510979  WILMINGTON          LOT 50              5.0    233.0   

           description gisacre  improvval            taxamt  \
0     PLANTATION LAKES     NaN    44500.0  133-16.00-343.00   
1     PLANTATION LAKES     NaN    43500.0  133-16.00-342.00   
2     PLANTATION LAKES     NaN    22700.0  133-16.00-334.00   
3             N/RT 329    8.04        NaN    133-6.00-23.07   
4  VINES CREEK VILLAGE     NaN        NaN  233-11.00-713.00   

                                            geometry  
0  POLYGON ((-8384050.109 4662665.268, -8384050.1...  
1  POLYGON ((-8384041.541 4662665.258, -8384041.5...  
2  POLYGON ((-8384034.478 4662714.131, -8384027.4...  
3  POLYGON ((-8390707.413 4668851.406, -8390913.5...  
4  POLYGON ((-8374845.075 4656982.198, -8374794.2...  

[5 rows x 27 columns]

In [ ]:
none_geometry_count = dataset['geometry'].isna().sum()
print(f"Number of rows with None geometry: {none_geometry_count}")

Number of rows with None geometry: 1


In [ ]:
dataset = dataset.dropna(subset=['geometry'])


In [ ]:
dataset.columns

Index(['ownfrst', 'ownlast', 'szip', 'parcel_id', 'additional_info', 'book',
       'front_footage', 'landval', 'zoning_type', 'assessment_value',
       'parcelnumb', 'description2', 'school_code', 'mailadd', 'state',
       'owner', 'town_code', 'shape', 'city', 'description1',
       'council_district', 'district', 'description', 'gisacre', 'improvval',
       'taxamt', 'geometry'],
      dtype='object')

In [ ]:
!pip install pyproj


In [ ]:
import pandas as pd
import geohash2
from shapely import wkt
from pyproj import Transformer
from shapely.ops import transform

# dataset['geometry'] = dataset['geometry'].apply(wkt.loads)

# Function to calculate the centroid of a polygon
def calculate_centroid_and_transform(polygon):
    # Calculate the centroid
    centroid = polygon.centroid
    # Transform the coordinates from EPSG:3857 (Pseudo-Mercator) to EPSG:4326 (WGS 84)
    transformer = Transformer.from_crs("epsg:3857", "epsg:4326", always_xy=True)
    longitude, latitude = transformer.transform(centroid.x, centroid.y)
    return longitude, latitude


def transform_geometry(geometry):
    transformer = Transformer.from_crs("epsg:3857", "epsg:4326", always_xy=True)
    return transform(transformer.transform, geometry)

# Initialize columns for geopoint and geohash
dataset['geopoint'] = None
dataset['geohash'] = None

# Calculate geopoint and geohash for each geometry
for index, row in dataset.iterrows():
    geometry = row['geometry']
    if geometry is not None:
        try:
            centroid_longitude, centroid_latitude = calculate_centroid_and_transform(geometry)
            transformed_geometry = transform_geometry(geometry)

            # Ensure longitude and latitude are within valid ranges
            if -180 <= centroid_longitude <= 180 and -90 <= centroid_latitude <= 90:
                geopoint = (centroid_latitude, centroid_longitude)
                geohash = geohash2.encode(centroid_latitude, centroid_longitude)
                dataset.at[index, 'geopoint'] = geopoint
                dataset.at[index, 'geohash'] = geohash
                dataset.at[index, 'transformed_geometry'] = transformed_geometry


            else:
                print(f"Invalid coordinates for row {index}: ({centroid_latitude}, {centroid_longitude})")
        except Exception as e:
            print(f"Error processing row {index}: {e}")
    else:
        print(f"No geometry for row {index}")

# Display the updated dataset
print(dataset[['geometry', 'geopoint', 'geohash']])




                                                 geometry  \
0       POLYGON ((-8384050.109 4662665.268, -8384050.1...   
1       POLYGON ((-8384041.541 4662665.258, -8384041.5...   
2       POLYGON ((-8384034.478 4662714.131, -8384027.4...   
3       POLYGON ((-8390707.413 4668851.406, -8390913.5...   
4       POLYGON ((-8374845.075 4656982.198, -8374794.2...   
...                                                   ...   
137324  MULTIPOLYGON (((-8361997.914 4659093.816, -836...   
137325  POLYGON ((-8361981.863 4660004.534, -8361972.6...   
137326  MULTIPOLYGON (((-8361359.986 4659826.878, -836...   
137327  MULTIPOLYGON (((-8365915.100 4676672.102, -836...   
137328  MULTIPOLYGON (((-8395546.461 4700305.096, -839...   

                                        geopoint       geohash  
0         (38.58673564473932, -75.3152422233462)  dqf7w0t058v5  
1        (38.58673557760311, -75.31516525907901)  dqf7w0t0j2y7  
2       (38.587078687638325, -75.31503183789339)  dqf7w0t608cf  
3      

In [ ]:
from shapely.geometry import shape, mapping, Polygon, MultiPolygon
def transform_geometry(geometry):
    """Transform the entire geometry from EPSG:3857 to EPSG:4326."""
    transformer = Transformer.from_crs("epsg:3857", "epsg:4326", always_xy=True)
    if isinstance(geometry, Polygon):
        transformed_coords = [transformer.transform(x, y) for x, y in geometry.exterior.coords]
        return MultiPolygon([Polygon(transformed_coords)])

In [ ]:
dataset['geometry'] = dataset['geometry'].apply(lambda geom : transform_geometry(geom))


KeyboardInterrupt: 

In [ ]:
dataset.head(10)

ownfrst           ownlast     szip    parcel_id additional_info  \
0           PATRICIA            HELWIG  19966.0  de-sx-343.0    TANYA CASSUP   
1  THOMAS & LISA KEE         MARSHALEK  19966.0  de-sx-342.0            None   
2  MEAGHAN ELIZABETH              MOHR  19966.0  de-sx-334.0            None   
3       DAVID MARTIN            PEPPER  19947.0  de-sx-23.07            None   
4               None  2026 VENTURE LLC  19804.0  de-sx-713.0            None   
5               None  2026 VENTURE LLC  19804.0  de-sx-712.0            None   
6               None  2026 VENTURE LLC  19804.0  de-sx-711.0            None   
7               None  2026 VENTURE LLC  19804.0  de-sx-710.0            None   
8               None  2026 VENTURE LLC  19804.0  de-sx-709.0            None   
9              DON S              HALL  19939.0   de-sx-73.0            None   

         book  front_footage  landval zoning_type assessment_value  ...  \
0  D 4110 179           22.0   5000.0        RS 0             None  ...   
1  D 3977 238           22.0   5000.0        RS 0             None  ...   
2  D 4011 310           18.0   5000.0        RS 0             None  ...   
3   D 539 271            NaN      NaN        FG 0             None  ...   
4  D 3420 251           75.0      NaN        TX 0             None  ...   
5  D 3420 251           79.0      NaN        TX 0             None  ...   
6  D 3420 251           96.0      NaN        TX 0             None  ...   
7  D 3420 251           82.0      NaN        TX 0             None  ...   
8  D 3420 251           83.0      NaN        TX 0             None  ...   
9  D 2582 325          150.0   3000.0        RS 0             None  ...   

   council_district district          description gisacre improvval  \
0               5.0    133.0     PLANTATION LAKES     NaN   44500.0   
1               5.0    133.0     PLANTATION LAKES     NaN   43500.0   
2               5.0    133.0     PLANTATION LAKES     NaN   22700.0   
3               2.0    133.0             N/RT 329    8.04       NaN   
4               5.0    233.0  VINES CREEK VILLAGE     NaN       NaN   
5               5.0    233.0  VINES CREEK VILLAGE     NaN       NaN   
6               5.0    233.0  VINES CREEK VILLAGE     NaN       NaN   
7               5.0    233.0  VINES CREEK VILLAGE     NaN       NaN   
8               5.0    233.0  VINES CREEK VILLAGE     NaN       NaN   
9               5.0    233.0           NW/RT 334A     NaN   17400.0   

             taxamt                                           geometry  \
0  133-16.00-343.00  POLYGON ((-8384050.109 4662665.268, -8384050.1...   
1  133-16.00-342.00  POLYGON ((-8384041.541 4662665.258, -8384041.5...   
2  133-16.00-334.00  POLYGON ((-8384034.478 4662714.131, -8384027.4...   
3    133-6.00-23.07  POLYGON ((-8390707.413 4668851.406, -8390913.5...   
4  233-11.00-713.00  POLYGON ((-8374845.075 4656982.198, -8374794.2...   
5  233-11.00-712.00  POLYGON ((-8374783.115 4656986.552, -8374784.0...   
6  233-11.00-711.00  POLYGON ((-8374778.604 4657009.585, -8374779.2...   
7  233-11.00-710.00  POLYGON ((-8374777.934 4657039.794, -8374777.6...   
8  233-11.00-709.00  POLYGON ((-8374791.671 4657093.315, -8374790.0...   
9    233-6.00-73.00  POLYGON ((-8376967.487 4659522.086, -8376906.9...   

                                   geopoint       geohash  \
0    (38.58673564473932, -75.3152422233462)  dqf7w0t058v5   
1   (38.58673557760311, -75.31516525907901)  dqf7w0t0j2y7   
2  (38.587078687638325, -75.31503183789339)  dqf7w0t608cf   
3   (38.63156512277316, -75.37535846243682)  dqf7ub9m4ven   
4   (38.54676549152905, -75.23234698829481)  dqfe211rpmbh   
5  (38.546952414880636, -75.23223224657879)  dqfe21383btz   
6  (38.547138051570705, -75.23214640538426)  dqfe21397gmg   
7   (38.54733692722831, -75.23215566150532)  dqfe213de8qv   
8  (38.547683255783575, -75.23227844093714)  dqfe213s8bgr   
9   (38.56443256337699, -75.25150003310212)  dqf7rs7w0gq8   

                                trans

In [ ]:
dataset.columns

Index(['ownfrst', 'ownlast', 'szip', 'parcel_id', 'additional_info', 'book',
       'front_footage', 'landval', 'zoning_type', 'assessment_value',
       'parcelnumb', 'description2', 'school_code', 'mailadd', 'state',
       'owner', 'town_code', 'shape', 'city', 'description1',
       'council_district', 'district', 'description', 'gisacre', 'improvval',
       'taxamt', 'geometry', 'geopoint', 'geohash', 'transformed_geometry'],
      dtype='object')

In [ ]:
dataset['geometry'].head(1)

0    POLYGON ((-8384050.109 4662665.268, -8384050.1...
Name: geometry, dtype: geometry

In [ ]:
dataset1 =  dataset
# Separate Geopoint into two columns: Latitude and Longitude
dataset1[['Latitude', 'Longitude']] = pd.DataFrame(dataset1['geopoint'].tolist(), index=dataset1.index)

# Convert the DataFrame to a GeoDataFrame
gdf1 = gpd.GeoDataFrame(dataset1, geometry='geometry')

# Drop the Geopoint column as it's no longer needed
gdf1.drop(columns=['geopoint'], inplace=True)

# Save the GeoDataFrame as a GeoJSON file
gdf1.to_file('/content/sussex-county-delaware-parcels', driver='GeoJSON')

In [ ]:
dataset.columns

Index(['ownfrst', 'ownlast', 'szip', 'parcel_id', 'additional_info', 'book',
       'front_footage', 'landval', 'zoning_type', 'assessment_value',
       'parcelnumb', 'description2', 'school_code', 'mailadd', 'state',
       'owner', 'town_code', 'shape', 'city', 'description1',
       'council_district', 'district', 'description', 'gisacre', 'improvval',
       'taxamt', 'geometry', 'geopoint', 'geohash', 'transformed_geometry'],
      dtype='object')

In [ ]:
dataset_copy = dataset


In [ ]:
import firebase_admin
from firebase_admin import credentials
from firebase_admin import firestore
import pandas as pd
import geopandas as gpd
from shapely.geometry import mapping
from shapely import wkt
import json

def convert_geometry_to_geojson_string(geometry):
    """Convert geometry to GeoJSON string."""
    geojson = mapping(geometry)
    coordinates = []
    for ring in geojson['coordinates']:
        formatted_ring = [list(coord) for coord in ring]
        coordinates.append(formatted_ring)
    geojson['coordinates'] = coordinates
    return json.dumps(geojson)


def save_dataframe_to_firestore(df, collection_name):
    """Save GeoDataFrame to Firestore."""
    # Create a GeoDataFrame from the existing DataFrame
    gdf = gpd.GeoDataFrame(df, geometry='geometry')

    # Initialize Firestore
    if not firebase_admin._apps:
        cred = credentials.Certificate('/content/usa-landiq-firebase-adminsdk-wzi8w-95c3e316cf.json')
        firebase_admin.initialize_app(cred)

    db = firestore.client()

    for index, row in gdf.iterrows():
        row_dict = row.to_dict()

        # Get the parcel_id to use as the document ID
        parcel_id = str(row_dict.get('parcel_id'))


        if 'geometry' in row_dict:
            geojson_string = convert_geometry_to_geojson_string(row_dict['geometry'])
            row_dict['geometry'] = json.loads(geojson_string)
        geopoint = row_dict.get('geopoint')
        if geopoint:
            latitude, longitude = geopoint
            geopoint = firestore.GeoPoint(latitude, longitude)
        # Extract geo-related data
        geo_data = {
            'geohash': row_dict.get('geohash'),
            'geopoint': geopoint
        }



        # Extract all other properties
        properties_data = {k: v for k, v in row_dict.items() if k not in ['geohash', 'geopoint', 'geometry', 'parcel_id']}
        coordinates_string = json.dumps(row_dict['geometry']['coordinates'])

        # Structure data for Firestore
        structured_data = {
            'geo': geo_data,
             'geometry': {
                'coordinates':  coordinates_string,
                'type': row_dict['geometry']['type']
            },

            'properties': properties_data
        }

        try:
            doc_ref = db.collection(collection_name).document(parcel_id)
            doc_ref.set(structured_data)
            print(f"Saved document with id: {doc_ref.id}")
        except Exception as e:
            print(f"Error saving document with parcel_id {parcel_id} at index {index}: {e}")
            print(f"Document data: {structured_data}")

# Assuming 'dataset' is your DataFrame
# Check if 'Geometry' needs to be converted
if isinstance(dataset_copy.loc[0, 'geometry'], str):
    # Convert 'Geometry' strings to Polygon objects
    dataset_copy['geometry'] = dataset_copy['geometry'].apply(wkt.loads)
else:
    dataset_copy['geometry'] = dataset_copy['geometry']



# Save the updated DataFrame to Firestore
collection_name = 'Sussex-County-parcels'
print(dataset_copy.head(5))
save_dataframe_to_firestore(dataset_copy, collection_name)

print("Data saved to Firestore successfully.")



             ownfrst           ownlast     szip    parcel_id additional_info  \
0           PATRICIA            HELWIG  19966.0  de-sx-343.0    TANYA CASSUP   
1  THOMAS & LISA KEE         MARSHALEK  19966.0  de-sx-342.0            None   
2  MEAGHAN ELIZABETH              MOHR  19966.0  de-sx-334.0            None   
3       DAVID MARTIN            PEPPER  19947.0  de-sx-23.07            None   
4               None  2026 VENTURE LLC  19804.0  de-sx-713.0            None   

         book  front_footage  landval zoning_type assessment_value  ...  \
0  D 4110 179           22.0   5000.0        RS 0             None  ...   
1  D 3977 238           22.0   5000.0        RS 0             None  ...   
2  D 4011 310           18.0   5000.0        RS 0             None  ...   
3   D 539 271            NaN      NaN        FG 0             None  ...   
4  D 3420 251           75.0      NaN        TX 0             None  ...   

   council_district district          description gisacre improvval 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Error saving document with parcel_id de-sx-1484.0 at index 2878: ('Cannot convert to a Firestore Value', <POLYGON ((-75.145 38.743, -75.145 38.744, -75.145 38.744, -75.145 38.743, -...>, 'Invalid type', <class 'shapely.geometry.polygon.Polygon'>)
Document data: {'geo': {'geohash': 'dqfs6j0c7yhs', 'geopoint': <google.cloud.firestore_v1._helpers.GeoPoint object at 0x7e33f5fb2bc0>}, 'geometry': {'coordinates': '[[[-8365133.521299999, 4684979.75], [-8365150.7938, 4685016.0205999985], [-8365136.6973, 4685022.788800001], [-8365119.4246, 4684986.518200003], [-8365133.521299999, 4684979.75]]]', 'type': 'Polygon'}, 'properties': {'ownfrst': 'GENO J & SUSAN A', 'ownlast': 'PELLECHIO', 'szip': 19422.0, 'additional_info': 'PELLECHIO', 'book': 'D 3150 13', 'front_footage': 40.0, 'landval': 10000.0, 'zoning_type': 'RS 0', 'assessment_value': None, 'parcelnumb': 1484.0, 'description2': None, 'school_code': 6.0, 'mailadd': '1069 WENTZ RD', 'state': 'PA', 'owner': 'PELLECHIO, GENO J & SUSAN A', 'town_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Error saving document with parcel_id de-sx-227.0 at index 5395: ('Cannot convert to a Firestore Value', <POLYGON ((-75.302 38.576, -75.302 38.576, -75.302 38.576, -75.302 38.576, -...>, 'Invalid type', <class 'shapely.geometry.polygon.Polygon'>)
Document data: {'geo': {'geohash': 'dqf7qqw3jw3u', 'geopoint': <google.cloud.firestore_v1._helpers.GeoPoint object at 0x7e33f5fb2650>}, 'geometry': {'coordinates': '[[[-8382611.009500001, 4661116.564900003], [-8382610.096999999, 4661113.636699997], [-8382610.1207, 4661110.564599998], [-8382611.0799, 4661107.648199998], [-8382612.881100001, 4661105.172899999], [-8382615.348200001, 4661103.380900003], [-8382643.130999999, 4661089.217200004], [-8382654.7521, 4661114.115599997], [-8382618.8343, 4661132.342200004], [-8382611.009500001, 4661116.564900003]]]', 'type': 'Polygon'}, 'properties': {'ownfrst': 'LLC', 'ownlast': 'HICKORY COMMONS', 'szip': 21122.0, 'additional_info': None, 'book': 'D 3035 348', 'front_footage': 45.0, 'landval': 3000.0, 'zoni

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

